In [58]:
import pandas as pd
import numpy as np
import plotly.express as px
from statistics import mode

# **Import data**

In [2]:
df = pd.read_csv("data/online_retail_II.csv")
df

Invoice StockCode                          Description  Quantity  \
0       489434     85048  15CM CHRISTMAS GLASS BALL 20 LIGHTS        12   
1       489434    79323P                   PINK CHERRY LIGHTS        12   
2       489434    79323W                  WHITE CHERRY LIGHTS        12   
3       489434     22041         RECORD FRAME 7" SINGLE SIZE         48   
4       489434     21232       STRAWBERRY CERAMIC TRINKET BOX        24   
...        ...       ...                                  ...       ...   
525456  538171     22271                 FELTCRAFT DOLL ROSIE         2   
525457  538171     22750         FELTCRAFT PRINCESS LOLA DOLL         1   
525458  538171     22751       FELTCRAFT PRINCESS OLIVIA DOLL         1   
525459  538171     20970   PINK FLORAL FELTCRAFT SHOULDER BAG         2   
525460  538171     21931               JUMBO STORAGE BAG SUKI         2   

             InvoiceDate  Price  Customer ID         Country  
0       01/12/2009 07:45   6.95      13085.0  United Kingdom  
1       01/12/2009 07:45   6.75      13085.0  United Kingdom  
2       01/12/2009 07:45   6.75      13085.0  United Kingdom  
3       01/12/2009 07:45   2.10      13085.0  United Kingdom  
4       01/12/2009 07:45   1.25      13085.0  United Kingdom  
...                  ...    ...          ...             ...  
525456  09/12/2010 20:01   2.95      17530.0  United Kingdom  
525457  09/12/2010 20:01   3.75      17530.0  United Kingdom  
525458  09/12/2010 20:01   3.75      17530.0  United Kingdom  
525459  09/12/2010 20:01   3.75      17530.0  United Kingdom  
525460  09/12/2010 20:01   1.95      17530.0  United Kingdom  

[525461 rows x 8 columns]

In [3]:
# Check preliminary info
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 525461 entries, 0 to 525460
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   Invoice      525461 non-null  object 
 1   StockCode    525461 non-null  object 
 2   Description  522533 non-null  object 
 3   Quantity     525461 non-null  int64  
 4   InvoiceDate  525461 non-null  object 
 5   Price        525461 non-null  float64
 6   Customer ID  417534 non-null  float64
 7   Country      525461 non-null  object 
dtypes: float64(2), int64(1), object(5)
memory usage: 32.1+ MB


# **Data cleaning**

- ## Fixing dtypes

Column `InvoiceDate` should be in datetime format.

In [4]:
df = df.astype({'InvoiceDate': 'datetime64'})

- ## Filtering prices and quantities

Only entries with prices greater than 0 ***and*** quantities greater than 0 should be kept:

In [5]:
n_original_rows = df.shape[0]
df = df.query("(Price > 0) & (Quantity > 0)")
rows_after = df.shape[0]

print(f"Total number of rows in the imported dataset (original): {n_original_rows}\n\
Number of rows after dropping: {rows_after}\n\
% of data removed: {100*(1-rows_after/n_original_rows):.2f}")

Total number of rows in the imported dataset (original): 525461
Number of rows after dropping: 511566
% of data removed: 2.64


- ## Fixing NA's 

In [6]:
# Check NA's in each column
df.isna().sum()

Invoice             0
StockCode           0
Description         0
Quantity            0
InvoiceDate         0
Price               0
Customer ID    103902
Country             0
dtype: int64

In [7]:
# Checking NA's from 'Customer ID'
df[df['Customer ID'].isna()]

Invoice StockCode                          Description  Quantity  \
577     489525    85226C            BLUE PULL BACK RACING CAR         1   
578     489525     85227          SET/6 3D KIT CARDS FOR KIDS         1   
1055    489548     22271                 FELTCRAFT DOLL ROSIE         1   
1056    489548     22254                 FELT TOADSTOOL LARGE        12   
1057    489548     22273                 FELTCRAFT DOLL MOLLY         3   
...        ...       ...                                  ...       ...   
525143  538154     82599          FANNY'S REST STOPMETAL SIGN         1   
525144  538154    84029E       RED WOOLLY HOTTIE WHITE HEART.         5   
525145  538154    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         4   
525146  538154    85099B              JUMBO BAG RED RETROSPOT         1   
525147  538154       DOT                       DOTCOM POSTAGE         1   

               InvoiceDate  Price  Customer ID         Country  
577    2009-01-12 11:49:00   0.55          NaN  United Kingdom  
578    2009-01-12 11:49:00   0.85          NaN  United Kingdom  
1055   2009-01-12 12:32:00   2.95          NaN  United Kingdom  
1056   2009-01-12 12:32:00   1.25          NaN  United Kingdom  
1057   2009-01-12 12:32:00   2.95          NaN  United Kingdom  
...                    ...    ...          ...             ...  
525143 2010-09-12 16:35:00   4.21          NaN  United Kingdom  
525144 2010-09-12 16:35:00   8.47          NaN  United Kingdom  
525145 2010-09-12 16:35:00   8.47          NaN  United Kingdom  
525146 2010-09-12 16:35:00   4.21          NaN  United Kingdom  
525147 2010-09-12 16:35:00  85.79          NaN  United Kingdom  

[103902 rows x 8 columns]

Apparently, these entries are valid. Let's keep them for now.

# **Data integrity**
#### (and maybe more cleaning!)

- ## Checking the `Invoice` column

Is it really an object-dtype column? Let's see which entries are not full numbers.

In [8]:
df[df.Invoice.str.contains("\D")]

Invoice StockCode Description  Quantity         InvoiceDate   Price  \
76799  C496350         M      Manual         1 2010-01-02 08:24:00  373.57   

       Customer ID         Country  
76799          NaN  United Kingdom

Only one entry (out of 511k+) is not a full-number invoice. Let's drop it and pretend nothing ever happened, 'kay? Let's also change the dtype of `Invoice` to `int`.

In [9]:
df = df.drop(76799).astype({"Invoice": "int32"})

What about the number of characters in each value of `Invoice`? Let's see...

In [10]:
df.Invoice.apply(lambda x: len(str(x))).value_counts()

6    511565
Name: Invoice, dtype: int64

Yay for consistency! No further steps are needed for this column (at least that's what we hope so).

- ## Checking the `StockCode` column

Let's take a look at the top-5 and bottom-5 values.

In [11]:
df.StockCode.value_counts()

85123A    3421
22423     2044
85099B    2012
21212     1920
21232     1713
          ... 
21860        1
20715        1
84572        1
84661a       1
22933        1
Name: StockCode, Length: 4251, dtype: int64

Right, so it's common to have letters and numbers as values. What about their lengths?

In [12]:
df['StockCode'].str.len().value_counts()

5     434882
6      73434
7        887
4        773
3        730
1        565
2        131
8         80
12        69
9         14
Name: StockCode, dtype: int64

Hmm, how would that look in a histogram?

In [13]:
aux = df['StockCode'].str.len()   #series containing the length of each value of 'StockCode'

px.histogram(aux)

Basically, anything not having 5 or 6 characters could potentially be an invalid StockCode (let's take that for granted, shall we?). We can't manually check every single value, but we can take a quick look over all the other non-5-non-6 values. Let's do it in batches, starting with values with length = 1, and then 2, etc.

# BUT,

before we continue, let's create an empty list named `removals`.

In this list we're gonna save all values that can be safely removed from the dataframe. Then, after all values *(really?)* of `StockCode` are checked, we can remove all these values at once. 

**"Why?"**, you may ask.

Right.

So... In order to keep using `aux` without warnings popping-up on the screen, we ought to keep the indexes of both the dataframe (`df`) and the series (`aux`) as it is, since they're matching perfectly (`aux` was created from an exact part (a column) of `df`). Removing values in between batches would cause the indexes to become misaligned.

In [14]:
removals = []

In [15]:
# Checking values with len = 1
df[aux == 1]

Invoice StockCode Description  Quantity         InvoiceDate   Price  \
2697     489609         M      Manual         1 2009-01-12 14:50:00    4.00   
11310    490300         M      Manual         1 2009-04-12 14:19:00    0.85   
11311    490300         M      Manual         1 2009-04-12 14:19:00    0.21   
17386    490760         M      Manual         1 2009-08-12 09:49:00   10.00   
17887    490881         M      Manual         1 2009-08-12 12:58:00   10.00   
...         ...       ...         ...       ...                 ...     ...   
517330   537534         M      Manual         1 2010-07-12 11:48:00  924.59   
521074   537800         M      Manual        12 2010-08-12 13:08:00    0.19   
521122   537804         M      Manual        12 2010-08-12 13:17:00    2.95   
521124   537804         M      Manual        12 2010-08-12 13:17:00    0.19   
524776   538147         M      Manual         1 2010-09-12 16:11:00   15.00   

        Customer ID         Country  
2697            NaN  United Kingdom  
11310       12970.0  United Kingdom  
11311       12970.0  United Kingdom  
17386       14295.0  United Kingdom  
17887       16210.0  United Kingdom  
...             ...             ...  
517330          NaN  United Kingdom  
521074      12748.0  United Kingdom  
521122      12748.0  United Kingdom  
521124      12748.0  United Kingdom  
524776      13090.0  United Kingdom  

[565 rows x 8 columns]

In [16]:
df[aux == 1]['StockCode'].value_counts()

M    555
D      5
m      4
S      1
Name: StockCode, dtype: int64

Hmm, multiple values. All `M` values seem to be associated with a `Manual` item. Let's make sure this is true.

In [17]:
df.query('StockCode == "M"')['Description'].value_counts()

Manual    555
Name: Description, dtype: int64

It is. Since these are not valid items, to the trash they go!

Let's check those `D`, `m` and `S` values all at once.

In [18]:
df[df.StockCode.apply(lambda x: x in['D', 'm', 'S'])]

Invoice StockCode Description  Quantity         InvoiceDate   Price  \
96608    498492         m      Manual         1 2010-02-19 10:56:00    2.55   
96609    498492         m      Manual         1 2010-02-19 10:56:00    3.40   
157226   504396         m      Manual         1 2010-04-13 11:45:00    4.00   
160443   504700         D    Discount         1 2010-04-15 18:08:00   57.63   
181508   506601         S     SAMPLES         1 2010-04-30 14:49:00   73.80   
212633   509979         D    Discount         1 2010-05-26 14:07:00  101.99   
228780   511509         m      Manual         1 2010-08-06 15:26:00    2.55   
312285   519808         D    Discount       192 2010-08-20 12:50:00    1.00   
494226   535657         D    Discount         1 2010-11-28 11:20:00   13.98   
501237   536158         D    Discount         1 2010-11-30 11:57:00   32.29   

        Customer ID         Country  
96608           NaN  United Kingdom  
96609           NaN  United Kingdom  
157226          NaN  United Kingdom  
160443      17032.0  United Kingdom  
181508          NaN  United Kingdom  
212633      12843.0  United Kingdom  
228780          NaN  United Kingdom  
312285      16422.0  United Kingdom  
494226      14527.0  United Kingdom  
501237      13634.0  United Kingdom

These are also trash. We can safely remove all values of `StockCode` with length = 1. Let's add them to our `removals` list.

In [19]:
removals += ['D', 'm', 'S', 'M']

In [20]:
# Checking values with len = 2
df[aux == 2]

Invoice StockCode Description  Quantity         InvoiceDate  Price  \
9292     490127        C2    CARRIAGE         1 2009-03-12 18:13:00   50.0   
14481    490541        C2    CARRIAGE         1 2009-07-12 09:25:00   50.0   
14502    490542        C2    CARRIAGE         1 2009-07-12 09:42:00   50.0   
19541    490998        C2    CARRIAGE         1 2009-08-12 17:24:00   50.0   
22803    491160        C2    CARRIAGE         1 2009-10-12 10:29:00   50.0   
...         ...       ...         ...       ...                 ...    ...   
504361   536540        C2    CARRIAGE         1 2010-01-12 14:05:00   50.0   
515057   537368        C2    CARRIAGE         1 2010-06-12 12:40:00   50.0   
515390   537378        C2    CARRIAGE         1 2010-06-12 13:06:00   50.0   
522913   537963        C2    CARRIAGE         1 2010-09-12 11:30:00   50.0   
522954   538002        C2    CARRIAGE         1 2010-09-12 11:48:00   50.0   

        Customer ID          Country  
9292        14156.0             EIRE  
14481           NaN             EIRE  
14502       14911.0             EIRE  
19541       16253.0   United Kingdom  
22803       14911.0             EIRE  
...             ...              ...  
504361      14911.0             EIRE  
515057      14911.0             EIRE  
515390      14911.0             EIRE  
522913      13369.0   United Kingdom  
522954      14932.0  Channel Islands  

[131 rows x 8 columns]

In [21]:
df[aux == 2].StockCode.value_counts()

C2    131
Name: StockCode, dtype: int64

C2? Carriage? Trash!

In [22]:
removals.append('C2')

In [23]:
# Checking values with len = 3
df[aux == 3]

Invoice StockCode     Description  Quantity         InvoiceDate  \
2379     489597       DOT  DOTCOM POSTAGE         1 2009-01-12 14:28:00   
2539     489600       DOT  DOTCOM POSTAGE         1 2009-01-12 14:43:00   
2551     489601       DOT  DOTCOM POSTAGE         1 2009-01-12 14:44:00   
2571     489602       DOT  DOTCOM POSTAGE         1 2009-01-12 14:45:00   
2619     489603       DOT  DOTCOM POSTAGE         1 2009-01-12 14:46:00   
...         ...       ...             ...       ...                 ...   
524272   538071       DOT  DOTCOM POSTAGE         1 2010-09-12 14:09:00   
524887   538148       DOT  DOTCOM POSTAGE         1 2010-09-12 16:26:00   
525000   538149       DOT  DOTCOM POSTAGE         1 2010-09-12 16:27:00   
525126   538153       DOT  DOTCOM POSTAGE         1 2010-09-12 16:31:00   
525147   538154       DOT  DOTCOM POSTAGE         1 2010-09-12 16:35:00   

         Price  Customer ID         Country  
2379    647.19          NaN  United Kingdom  
2539     55.96          NaN  United Kingdom  
2551     68.39          NaN  United Kingdom  
2571     59.35          NaN  United Kingdom  
2619     42.39          NaN  United Kingdom  
...        ...          ...             ...  
524272  885.94          NaN  United Kingdom  
524887  547.32          NaN  United Kingdom  
525000  620.68          NaN  United Kingdom  
525126  822.94          NaN  United Kingdom  
525147   85.79          NaN  United Kingdom  

[730 rows x 8 columns]

In [24]:
df[aux == 3].StockCode.value_counts()

DOT    730
Name: StockCode, dtype: int64

Apparently, all length = 3 values are not items by themselves. `DOT` should be added to our list.

In [25]:
removals.append('DOT')

In [26]:
# Checking values with len = 4
df[aux == 4]

Invoice StockCode Description  Quantity         InvoiceDate  Price  \
89       489439      POST     POSTAGE         3 2009-01-12 09:28:00   18.0   
126      489444      POST     POSTAGE         1 2009-01-12 09:55:00  141.0   
173      489447      POST     POSTAGE         1 2009-01-12 10:10:00  130.0   
625      489526      POST     POSTAGE         6 2009-01-12 11:50:00   18.0   
1244     489557      POST     POSTAGE         4 2009-01-12 12:52:00   18.0   
...         ...       ...         ...       ...                 ...    ...   
522916   537967      POST     POSTAGE         1 2010-09-12 11:31:00   18.0   
522930   537995      POST     POSTAGE         2 2010-09-12 11:39:00   18.0   
522974   538003      POST     POSTAGE         8 2010-09-12 12:05:00   18.0   
523064   538008      POST     POSTAGE         5 2010-09-12 12:17:00   18.0   
524491   538093      POST     POSTAGE         5 2010-09-12 14:49:00   18.0   

        Customer ID  Country  
89          12682.0   France  
126         12636.0      USA  
173         12362.0  Belgium  
625         12533.0  Germany  
1244        12490.0   France  
...             ...      ...  
522916      12494.0   France  
522930      12712.0  Germany  
522974      12429.0  Denmark  
523064      12683.0   France  
524491      12682.0   France  

[773 rows x 8 columns]

In [27]:
df[aux == 4].StockCode.value_counts()

POST    759
PADS     14
Name: StockCode, dtype: int64

In [28]:
df.query('StockCode == "PADS"')

Invoice StockCode                 Description  Quantity  \
62299    494914      PADS  PADS TO MATCH ALL CUSHIONS         1   
74731    496222      PADS  PADS TO MATCH ALL CUSHIONS         1   
77702    496473      PADS  PADS TO MATCH ALL CUSHIONS         1   
79794    496643      PADS  PADS TO MATCH ALL CUSHIONS         1   
90798    497935      PADS  PADS TO MATCH ALL CUSHIONS         1   
97716    498562      PADS  PADS TO MATCH ALL CUSHIONS         1   
101718   499056      PADS  PADS TO MATCH ALL CUSHIONS         1   
104480   499399      PADS  PADS TO MATCH ALL CUSHIONS         1   
123947   501176      PADS  PADS TO MATCH ALL CUSHIONS         1   
156809   504332      PADS  PADS TO MATCH ALL CUSHIONS         1   
178629   506303      PADS  PADS TO MATCH ALL CUSHIONS         1   
341826   522766      PADS  PADS TO MATCH ALL CUSHIONS         1   
440930   531433      PADS  PADS TO MATCH ALL CUSHIONS         1   
468280   533528      PADS  PADS TO MATCH ALL CUSHIONS         1   

               InvoiceDate  Price  Customer ID         Country  
62299  2010-01-19 17:04:00  0.001      16705.0  United Kingdom  
74731  2010-01-29 13:53:00  0.001      13583.0  United Kingdom  
77702  2010-01-02 15:38:00  0.001      17350.0  United Kingdom  
79794  2010-03-02 11:58:00  0.001      13408.0  United Kingdom  
90798  2010-02-15 10:47:00  0.001      13408.0  United Kingdom  
97716  2010-02-21 12:03:00  0.001      15182.0  United Kingdom  
101718 2010-02-24 13:46:00  0.001      13765.0  United Kingdom  
104480 2010-02-26 13:26:00  0.001      14459.0  United Kingdom  
123947 2010-03-15 11:00:00  0.001      14857.0  United Kingdom  
156809 2010-12-04 16:30:00  0.001      12671.0         Germany  
178629 2010-04-29 10:43:00  0.001      14249.0  United Kingdom  
341826 2010-09-16 13:58:00  0.001      15182.0  United Kingdom  
440930 2010-08-11 11:54:00  0.001      13317.0  United Kingdom  
468280 2010-11-17 15:08:00  0.001      15750.0  United Kingdom

Both values are trash, really. You can keep them if you want, but I am not.

In [29]:
removals += ['PADS', 'POST']

In [30]:
# Checking values with len = 7
df[aux == 7]

Invoice StockCode               Description  Quantity  \
572      489522   79323LP  LIGHT PINK CHERRY LIGHTS         1   
613      489526   15056BL   EDWARDIAN PARASOL BLACK         6   
2620     489604   15056bl   EDWARDIAN PARASOL BLACK         1   
3142     489658   15056BL   EDWARDIAN PARASOL BLACK        12   
3158     489658   79323LP  LIGHT PINK CHERRY LIGHTS         6   
...         ...       ...                       ...       ...   
519063   537645   15056bl   EDWARDIAN PARASOL BLACK         2   
520482   537769   15056BL   EDWARDIAN PARASOL BLACK         2   
524462   538093   15056BL   EDWARDIAN PARASOL BLACK        12   
524777   538148   15056bl   EDWARDIAN PARASOL BLACK         3   
525006   538153   15056bl   EDWARDIAN PARASOL BLACK         1   

               InvoiceDate  Price  Customer ID         Country  
572    2009-01-12 11:45:00   6.75      15998.0  United Kingdom  
613    2009-01-12 11:50:00   5.95      12533.0         Germany  
2620   2009-01-12 14:47:00  13.00          NaN  United Kingdom  
3142   2009-01-12 17:31:00   5.95      15485.0  United Kingdom  
3158   2009-01-12 17:31:00   6.75      15485.0  United Kingdom  
...                    ...    ...          ...             ...  
519063 2010-07-12 15:34:00  12.72          NaN  United Kingdom  
520482 2010-08-12 12:17:00   5.95      15021.0  United Kingdom  
524462 2010-09-12 14:49:00   5.95      12682.0          France  
524777 2010-09-12 16:26:00  12.72          NaN  United Kingdom  
525006 2010-09-12 16:31:00  12.72          NaN  United Kingdom  

[887 rows x 8 columns]

In [31]:
df[aux == 7].StockCode.value_counts()

15056BL    589
79323LP    170
79323GR     83
15056bl     31
TEST001      9
ADJUST2      3
47503J       1
TEST002      1
Name: StockCode, dtype: int64

Ok, these lists are getting bigger... From a quick glance, we can assume that:
- `15056BL` and `15056bl` are probably the same item
- `TEST001` is not a valid item
- `ADJUST2` is not valid either
- `79323LP` and `79323GR` have the same numbers, but different letters (why is that?)
- `47503J` is all by itself... Is it a rare item or just a glitch in the matrix?

The answers are down below, in the next few cells.

In [32]:
df.query("StockCode == '15056BL' | StockCode == '15056bl'").head()

Invoice StockCode              Description  Quantity  \
613    489526   15056BL  EDWARDIAN PARASOL BLACK         6   
2620   489604   15056bl  EDWARDIAN PARASOL BLACK         1   
3142   489658   15056BL  EDWARDIAN PARASOL BLACK        12   
3290   489675   15056BL  EDWARDIAN PARASOL BLACK       240   
3923   489789   15056BL  EDWARDIAN PARASOL BLACK         3   

             InvoiceDate  Price  Customer ID         Country  
613  2009-01-12 11:50:00   5.95      12533.0         Germany  
2620 2009-01-12 14:47:00  13.00          NaN  United Kingdom  
3142 2009-01-12 17:31:00   5.95      15485.0  United Kingdom  
3290 2009-02-12 09:47:00   4.60      13777.0  United Kingdom  
3923 2009-02-12 11:59:00   5.95      15833.0  United Kingdom

In [33]:
df.query("StockCode == '15056BL' | StockCode == '15056bl'")['Description'].value_counts()

EDWARDIAN PARASOL BLACK    620
Name: Description, dtype: int64

Yes, they are the same item. Yes, they are valid.

We should take a moment to fix this lowercase/uppercase problem we just had. By default, StockCodes are all uppercase, so let's turn all entries into uppercases.

In [34]:
df['StockCode'] = df['StockCode'].apply(str.upper)

In [35]:
df.query("StockCode == 'ADJUST2' | StockCode == 'TEST001'")

Invoice StockCode                          Description  Quantity  \
27994    491725   TEST001              This is a test product.        10   
28251    491742   TEST001              This is a test product.         5   
28254    491744   TEST001              This is a test product.         5   
39398    492718   TEST001              This is a test product.         5   
45228    493410   TEST001              This is a test product.         5   
45230    493412   TEST001              This is a test product.         5   
56117    494450   TEST001              This is a test product.         5   
66084    495295   TEST001              This is a test product.         5   
156017   504188   TEST001              This is a test product.         5   
249672   513564   ADJUST2  Adjustment by Peter on Jun 25 2010          1   
249673   513566   ADJUST2  Adjustment by Peter on Jun 25 2010          1   
249674   513565   ADJUST2  Adjustment by Peter on Jun 25 2010          1   

               InvoiceDate   Price  Customer ID         Country  
27994  2009-12-14 08:34:00    4.50      12346.0  United Kingdom  
28251  2009-12-14 11:00:00    4.50      12346.0  United Kingdom  
28254  2009-12-14 11:02:00    4.50      12346.0  United Kingdom  
39398  2009-12-18 10:47:00    4.50      12346.0  United Kingdom  
45228  2010-04-01 09:24:00    4.50      12346.0  United Kingdom  
45230  2010-04-01 09:53:00    4.50      12346.0  United Kingdom  
56117  2010-01-14 13:50:00    4.50      12346.0  United Kingdom  
66084  2010-01-22 13:30:00    4.50      12346.0  United Kingdom  
156017 2010-12-04 09:52:00    4.50      16454.0  United Kingdom  
249672 2010-06-25 14:15:00  300.13      17050.0  United Kingdom  
249673 2010-06-25 14:15:00  358.47      17364.0  United Kingdom  
249674 2010-06-25 14:15:00   72.45      16422.0  United Kingdom

Trash. Clearly.

In [36]:
df.query("StockCode == '79323LP' | StockCode == '79323GR'")

Invoice StockCode               Description  Quantity  \
572      489522   79323LP  LIGHT PINK CHERRY LIGHTS         1   
3158     489658   79323LP  LIGHT PINK CHERRY LIGHTS         6   
3173     489664   79323GR       GREEN CHERRY LIGHTS         2   
3467     489688   79323LP  LIGHT PINK CHERRY LIGHTS        24   
4037     489792   79323LP  LIGHT PINK CHERRY LIGHTS         2   
...         ...       ...                       ...       ...   
163046   504913   79323LP  LIGHT PINK CHERRY LIGHTS         4   
166689   505177   79323GR       GREEN CHERRY LIGHTS         1   
166690   505177   79323LP  LIGHT PINK CHERRY LIGHTS         2   
308605   519514   79323LP  LIGHT PINK CHERRY LIGHTS        72   
413967   528949   79323LP  LIGHT PINK CHERRY LIGHTS         6   

               InvoiceDate  Price  Customer ID         Country  
572    2009-01-12 11:45:00   6.75      15998.0  United Kingdom  
3158   2009-01-12 17:31:00   6.75      15485.0  United Kingdom  
3173   2009-01-12 18:03:00   6.75      14061.0  United Kingdom  
3467   2009-02-12 10:42:00   5.45      14894.0  United Kingdom  
4037   2009-02-12 12:06:00   6.75      14527.0  United Kingdom  
...                    ...    ...          ...             ...  
163046 2010-04-19 10:04:00   6.75      14911.0            EIRE  
166689 2010-04-20 13:43:00   6.75      13042.0  United Kingdom  
166690 2010-04-20 13:43:00   6.75      13042.0  United Kingdom  
308605 2010-08-18 09:19:00   5.45      14156.0            EIRE  
413967 2010-10-25 16:08:00   6.75      14911.0            EIRE  

[253 rows x 8 columns]

Looks like those last two letters refer to the color of the lights. These are valid items.

In [37]:
df.query("StockCode == '47503J'")

Invoice StockCode                       Description  Quantity  \
2981     489642    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
9784     490149    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
15894    490711    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
20061    491041    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
27489    491702    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         6   
...         ...       ...                               ...       ...   
356535   524004    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
496010   535803    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         6   
496295   535811    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
509364   536945    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         1   
519338   537654    47503J  SET/3 FLORAL GARDEN TOOLS IN BAG         2   

               InvoiceDate  Price  Customer ID         Country  
2981   2009-01-12 16:19:00   7.95          NaN  United Kingdom  
9784   2009-04-12 09:43:00  16.48          NaN  United Kingdom  
15894  2009-07-12 15:26:00   7.95      17841.0  United Kingdom  
20061  2009-09-12 09:42:00  16.48          NaN  United Kingdom  
27489  2009-12-13 13:53:00   7.95          NaN            EIRE  
...                    ...    ...          ...             ...  
356535 2010-09-26 16:06:00   7.95      15532.0  United Kingdom  
496010 2010-11-28 14:57:00   7.95      14410.0  United Kingdom  
496295 2010-11-28 15:18:00   7.95      15532.0  United Kingdom  
509364 2010-03-12 12:24:00   7.95      14083.0  United Kingdom  
519338 2010-07-12 15:59:00   7.95          NaN  United Kingdom  

[75 rows x 8 columns]

Also valid.

Adding trash to the trashcan:

In [38]:
removals += ['TEST001', 'ADJUST2']

In [39]:
# Checking values with len = 8
df[aux == 8]

Invoice StockCode                   Description  Quantity  \
2377     489597  DCGS0058              MISO PRETTY  GUM         1   
2378     489597  DCGS0068             DOGS NIGHT COLLAR         1   
8371     490074  DCGS0004    HAYNES CAMPER SHOULDER BAG         1   
8372     490074  DCGS0058              MISO PRETTY  GUM         1   
8373     490074  DCGS0076  SUNJAR LED NIGHT NIGHT LIGHT         1   
...         ...       ...                           ...       ...   
466307   533348  DCGS0003           BOXED GLASS ASHTRAY         1   
466308   533348  DCGSSBOY                BOYS PARTY BAG         1   
478086   534289  DCGS0003           BOXED GLASS ASHTRAY         1   
496962   535835  DCGSSBOY                BOYS PARTY BAG         3   
524271   538071  DCGS0076  SUNJAR LED NIGHT NIGHT LIGHT         1   

               InvoiceDate  Price  Customer ID         Country  
2377   2009-01-12 14:28:00   0.83          NaN  United Kingdom  
2378   2009-01-12 14:28:00   8.65          NaN  United Kingdom  
8371   2009-03-12 14:39:00  17.35          NaN  United Kingdom  
8372   2009-03-12 14:39:00   0.83          NaN  United Kingdom  
8373   2009-03-12 14:39:00  16.48          NaN  United Kingdom  
...                    ...    ...          ...             ...  
466307 2010-11-17 09:23:00   2.51          NaN  United Kingdom  
466308 2010-11-17 09:23:00   3.36          NaN  United Kingdom  
478086 2010-11-22 11:25:00   2.51          NaN  United Kingdom  
496962 2010-11-29 09:46:00   3.36          NaN  United Kingdom  
524271 2010-09-12 14:09:00  16.13          NaN  United Kingdom  

[80 rows x 8 columns]

In [40]:
df[aux == 8].StockCode.value_counts()

DCGS0058    30
DCGS0076    13
DCGSSBOY    10
DCGS0003     9
DCGS0069     4
DCGS0072     3
DCGS0004     3
DCGS0068     2
DCGS0062     1
DCGS0037     1
DCGS0044     1
DCGS0070     1
DCGS0075     1
DCGS0041     1
Name: StockCode, dtype: int64

Ugh, lengthy... We can't manually check each one of these entries, but they seem to be valid. Next.

In [41]:
# Checking values with len = 9
df[aux == 9]

Invoice  StockCode              Description  Quantity  \
44245    493265  DCGS0066N  NAVY CUDDLES DOG HOODIE         1   
44377    493269  DCGS0066N  NAVY CUDDLES DOG HOODIE         1   
244831   513099  DCGSSGIRL          GIRLS PARTY BAG         3   
246184   513200  DCGSSGIRL          GIRLS PARTY BAG         6   
249938   513574  DCGSSGIRL          GIRLS PARTY BAG         1   
251930   513655  DCGSSGIRL          GIRLS PARTY BAG         5   
253997   513907  DCGSSGIRL          GIRLS PARTY BAG         1   
385192   526405  DCGSSGIRL          GIRLS PARTY BAG         6   
425616   530060  DCGSSGIRL          GIRLS PARTY BAG         2   
427107   530140  DCGSSGIRL          GIRLS PARTY BAG        12   
440698   531411  AMAZONFEE               AMAZON FEE         1   
465555   533338  DCGSSGIRL          GIRLS PARTY BAG         6   
496963   535835  DCGSSGIRL          GIRLS PARTY BAG         3   
517955   537632  AMAZONFEE               AMAZON FEE         1   

               InvoiceDate     Price  Customer ID         Country  
44245  2009-12-22 15:05:00      8.65          NaN  United Kingdom  
44377  2009-12-22 15:07:00      8.65          NaN  United Kingdom  
244831 2010-06-21 15:13:00      3.36          NaN  United Kingdom  
246184 2010-06-22 16:28:00      3.36          NaN  United Kingdom  
249938 2010-06-25 15:13:00      3.36          NaN  United Kingdom  
251930 2010-06-28 10:02:00      3.36          NaN  United Kingdom  
253997 2010-06-29 12:08:00      3.36          NaN  United Kingdom  
385192 2010-11-10 13:53:00      3.36          NaN  United Kingdom  
425616 2010-01-11 11:35:00      3.36          NaN  United Kingdom  
427107 2010-01-11 16:45:00      3.36          NaN  United Kingdom  
440698 2010-08-11 10:11:00   6706.71          NaN  United Kingdom  
465555 2010-11-16 18:18:00      3.36          NaN  United Kingdom  
496963 2010-11-29 09:46:00      3.36          NaN  United Kingdom  
517955 2010-07-12 15:08:00  13541.33          NaN  United Kingdom

In [42]:
df[aux == 9].StockCode.value_counts()

DCGSSGIRL    10
DCGS0066N     2
AMAZONFEE     2
Name: StockCode, dtype: int64

`AMAZONFEE`? No way!

In [43]:
df.query("StockCode == 'AMAZONFEE'")

Invoice  StockCode Description  Quantity         InvoiceDate  \
440698   531411  AMAZONFEE  AMAZON FEE         1 2010-08-11 10:11:00   
517955   537632  AMAZONFEE  AMAZON FEE         1 2010-07-12 15:08:00   

           Price  Customer ID         Country  
440698   6706.71          NaN  United Kingdom  
517955  13541.33          NaN  United Kingdom

Needless to say.

In [44]:
removals.append('AMAZONFEE')

In [45]:
# Checking values with len = 12 (finally!)
df[aux == 12]

Invoice     StockCode                         Description  Quantity  \
18466    490948  BANK CHARGES                        Bank Charges         1   
31079    491969  GIFT_0001_80  Dotcomgiftshop Gift Voucher £80.00         1   
32048    491971  GIFT_0001_20  Dotcomgiftshop Gift Voucher £20.00         2   
40904    492782  GIFT_0001_10  Dotcomgiftshop Gift Voucher £10.00         1   
40905    492782  GIFT_0001_20  Dotcomgiftshop Gift Voucher £20.00         1   
...         ...           ...                                 ...       ...   
442201   531489  GIFT_0001_10  Dotcomgiftshop Gift Voucher £10.00         1   
455268   532637  BANK CHARGES                        Bank Charges         1   
492078   535407  GIFT_0001_20  Dotcomgiftshop Gift Voucher £20.00         1   
493162   535474  BANK CHARGES                        Bank Charges         1   
507344   536779  BANK CHARGES                        Bank Charges         1   

               InvoiceDate  Price  Customer ID         Country  
18466  2009-08-12 14:29:00  15.00      16805.0  United Kingdom  
31079  2009-12-14 17:57:00  69.56          NaN  United Kingdom  
32048  2009-12-14 18:37:00  17.39          NaN  United Kingdom  
40904  2009-12-18 17:06:00   8.69          NaN  United Kingdom  
40905  2009-12-18 17:06:00  17.39          NaN  United Kingdom  
...                    ...    ...          ...             ...  
442201 2010-08-11 15:02:00   8.51          NaN  United Kingdom  
455268 2010-12-11 16:18:00  15.00      13174.0  United Kingdom  
492078 2010-11-26 11:20:00  17.02          NaN  United Kingdom  
493162 2010-11-26 13:56:00  15.00      16928.0  United Kingdom  
507344 2010-02-12 15:08:00  15.00      15823.0  United Kingdom  

[69 rows x 8 columns]

In [46]:
df[aux == 12].StockCode.value_counts()

BANK CHARGES    23
GIFT_0001_20    17
GIFT_0001_30    17
GIFT_0001_10     6
GIFT_0001_50     2
GIFT_0001_40     2
GIFT_0001_70     1
GIFT_0001_80     1
Name: StockCode, dtype: int64

Yay for gift vouchers, nay for bank charges! Trash 'em.

In [47]:
removals.append('BANK CHARGES')

Only selecting entries not in `removals`:

In [48]:
df = df.query("StockCode not in @removals")

- ## Checking the `Description` column

In [49]:
df['Description'].value_counts()

WHITE HANGING HEART T-LIGHT HOLDER    3455
REGENCY CAKESTAND 3 TIER              2044
STRAWBERRY CERAMIC TRINKET BOX        1713
PACK OF 72 RETRO SPOT CAKE CASES      1456
ASSORTED COLOUR BIRD ORNAMENT         1449
                                      ... 
BOX OF 3 PEBBLE CANDLES                  1
BAG FOR CHILDREN VINTAGE BLUE            1
JADE GREEN PAIR ENAMEL HAIR SLIDES       1
GOLD CHRISTMAS STOCKING DECORATION       1
ANGEL ON KNEES METAL POLE 100CM H        1
Name: Description, Length: 4523, dtype: int64

I don't feel like going through 4523 different items, so we'll just assume everything is fine with this column. Next customer, please.

- ## Checking the `Quantity`, `InvoiceDate`, `Price` columns

`Quantity` and `Price` are just fine, they were cleaned in the first steps.

`InvoiceDate` didn't have any NA's and pandas had no trouble converting all of its values to datetime format. Checking the first and last days in the column:

In [50]:
df.InvoiceDate.sort_values()

0        2009-01-12 07:45:00
1        2009-01-12 07:45:00
2        2009-01-12 07:45:00
3        2009-01-12 07:45:00
4        2009-01-12 07:45:00
                 ...        
455459   2010-12-11 17:00:00
455454   2010-12-11 17:00:00
455364   2010-12-11 17:00:00
455782   2010-12-11 17:01:00
455783   2010-12-11 17:32:00
Name: InvoiceDate, Length: 509329, dtype: datetime64[ns]

All good. Let's press on.

- ## Checking the `Customer ID` column

In [51]:
df['Customer ID'].value_counts()

14911.0    5488
17841.0    5042
14606.0    3857
14156.0    2623
12748.0    2615
           ... 
18227.0       1
14106.0       1
13438.0       1
16990.0       1
13551.0       1
Name: Customer ID, Length: 4295, dtype: int64

In [52]:
df['Customer ID'].apply(str).str.len().value_counts()

7    406330
3    102999
Name: Customer ID, dtype: int64

In [53]:
df['Customer ID'].apply(lambda x: len(str(x))).value_counts()   #using str() since len() can't be applied to int's

7    406330
3    102999
Name: Customer ID, dtype: int64

Apparently all customer ID's are valid. They either have 5 digits (we used the `len()` function on numbers ending in `.0`) or are NA's (NA's are represented by `NaN`, which has len = 3 if converted to a string).

- ## Checking the `Country` column

In [54]:
df.Country.value_counts()

United Kingdom          472033
EIRE                      9339
Germany                   7379
France                    5351
Netherlands               2661
Spain                     1198
Switzerland               1146
Portugal                  1034
Belgium                    988
Sweden                     859
Channel Islands            817
Italy                      696
Australia                  625
Cyprus                     539
Greece                     511
Austria                    504
Denmark                    408
United Arab Emirates       395
Norway                     362
Finland                    339
Unspecified                306
USA                        225
Poland                     181
Malta                      168
Japan                      164
Lithuania                  154
Singapore                  117
RSA                        109
Bahrain                    106
Canada                      77
Thailand                    76
Israel                      74
Hong Kon

`Unspecified`? Let's look at it.

In [55]:
df.query('Country == "Unspecified"')

Invoice StockCode                        Description  Quantity  \
61394    494860     84832   ZINC WILLIE WINKIE  CANDLE STICK         5   
61395    494860     84836        ZINC METAL HEART DECORATION         5   
61396    494860    85014D   PINK/BROWN DOTS RUFFLED UMBRELLA         1   
61397    494860    85014A   BLACK/BLUE DOTS RUFFLED UMBRELLA         1   
61398    494860    85014B    RED/WHITE DOTS RUFFLED UMBRELLA         2   
...         ...       ...                                ...       ...   
499215   536012     79000                 MOROCCAN TEA GLASS        12   
499216   536012     22665  RECIPE BOX BLUE SKETCHBOOK DESIGN         6   
499217   536012     20886            BOX OF 9 PEBBLE CANDLES         6   
499218   536012     22424             ENAMEL BREAD BIN CREAM         1   
499219   536012     22441  GROW YOUR OWN BASIL IN ENAMEL MUG         8   

               InvoiceDate  Price  Customer ID      Country  
61394  2010-01-19 11:01:00   0.85      12470.0  Unspecified  
61395  2010-01-19 11:01:00   1.25      12470.0  Unspecified  
61396  2010-01-19 11:01:00   5.95      12470.0  Unspecified  
61397  2010-01-19 11:01:00   5.95      12470.0  Unspecified  
61398  2010-01-19 11:01:00   5.95      12470.0  Unspecified  
...                    ...    ...          ...          ...  
499215 2010-11-29 15:23:00   0.85      12351.0  Unspecified  
499216 2010-11-29 15:23:00   2.95      12351.0  Unspecified  
499217 2010-11-29 15:23:00   1.95      12351.0  Unspecified  
499218 2010-11-29 15:23:00  12.75      12351.0  Unspecified  
499219 2010-11-29 15:23:00   2.10      12351.0  Unspecified  

[306 rows x 8 columns]

These look like valid orders, let's keep 'em.

Before we dig deeper into our data, let's see how many rows we have gotten rid of.

In [56]:
print(f"Total number of rows in the imported dataset (original): {n_original_rows}\n\
Number of rows at the moment: {df.shape[0]}\n\
% of data removed so far: {100*(1-df.shape[0]/n_original_rows):.2f}")

Total number of rows in the imported dataset (original): 525461
Number of rows at the moment: 509329
% of data removed so far: 3.07


- ## Grouping all items according to their invoices

In [59]:
invoices = df.groupby(['Invoice']).agg({'Quantity': 'sum',
                                        'Price': 'sum',
                                        'Customer ID': mode})   # you never know when this might come in handy
invoices

Quantity   Price  Customer ID
Invoice                               
489434        166   32.65      13085.0
489435         60   10.50      13085.0
489436        193   70.88      13078.0
489437        145   83.45      15362.0
489438        826   44.05      18102.0
...           ...     ...          ...
538167        125   76.15      14713.0
538168        167   68.95      14702.0
538169         33   39.20      13230.0
538170        133   70.54      13969.0
538171        194  165.58      17530.0

[20610 rows x 3 columns]

In [60]:
invoices['Customer ID'].apply(str).str.len().value_counts()

7    18999
3     1611
Name: Customer ID, dtype: int64

In [61]:
print(f"The number of unique invoices is: {invoices.shape[0]}")

The number of unique invoices is: 20610


In [62]:
invoices.describe()

Quantity         Price   Customer ID
count  20610.000000  20610.000000  18999.000000
mean     282.660747     84.892517  15352.647297
std     1379.843699    183.924382   1706.060210
min        1.000000      0.090000  12346.000000
25%       63.000000     18.050000  13878.000000
50%      144.000000     46.225000  15298.000000
75%      281.000000     89.480000  16843.000000
max    87167.000000   5117.030000  18287.000000

Apart from that Customer ID column, the other columns in the `describe()` dataframe gives us very precious information:
- 75% of all invoices had

In [64]:
px.box(invoices['Price'])

# **Data analysis**

- ## Which countries had the most orders?

In [ ]:
df.groupby('Country')['Quantity'].count().sort_values(ascending=False)[:5]

Country
United Kingdom    473378
EIRE                9459
Germany             7654
France              5532
Netherlands         2729
Name: Quantity, dtype: int64

- ## Which invoices had the most items?

In [ ]:
df.groupby('Invoice')['Quantity'].sum().sort_values(ascending=False)[:5]

Invoice
518505    87167
524174    87167
497946    83774
501534    63974
495194    63302
Name: Quantity, dtype: int64

- ## Which invoices were the most expensive?

Pssst! For that, we need a new column (`Revenue`) containing the revenue from sale for each item, since the values in the `Price` column refer to unit prices.

In [ ]:
df['Revenue'] = df['Price'] * df['Quantity']

In [ ]:
df.groupby('Invoice')['Revenue'].sum().sort_values(ascending=False)[:5]

Invoice
533027    49844.99
531516    45332.97
493819    44051.60
524181    33167.80
526934    26007.08
Name: Revenue, dtype: float64

- ## What are the most expensive items?

In [ ]:
df[['Description', 'Price']].sort_values(by='Price', ascending=False)[:5]

Description     Price
241827      Manual  25111.09
517955  AMAZON FEE  13541.33
135013      Manual  10953.50
135015      Manual  10953.50
372834      Manual  10468.80

***Excuse me?*** What is that?

Maybe we 